In [3]:
!pip install ultralytics

Defaulting to user installation because normal site-packages is not writeable


In [4]:
# Python function to automatically create data.yaml config file
# 1. Reads "classes.txt" file to get list of class names
# 2. Creates data dictionary with correct paths to folders, number of classes, and names of classes
# 3. Writes data in YAML format to data.yaml

import yaml
import os

def create_data_yaml(path_to_classes_txt, path_to_data_yaml):

  # Read class.txt to get class names
  if not os.path.exists(path_to_classes_txt):
    print(f'classes.txt file not found! Please create a classes.txt labelmap and move it to {path_to_classes_txt}')
    return
  with open(path_to_classes_txt, 'r') as f:
    classes = []
    for line in f.readlines():
      if len(line.strip()) == 0: continue
      classes.append(line.strip())
  number_of_classes = len(classes)

  # Create data dictionary
  data = {
      'path': 'data',
      'train': 'train/images',
      'val': 'validation/images',
      'nc': number_of_classes,
      'names': classes
  }

  # Write data to YAML file
  with open(path_to_data_yaml, 'w') as f:
    yaml.dump(data, f, sort_keys=False)
  print(f'Created config file at {path_to_data_yaml}')

  return

# Define path to classes.txt and run function
path_to_classes_txt = 'data/custom_data/Preprocesed Data/classes.txt'
path_to_data_yaml = 'data/data.yaml'

create_data_yaml(path_to_classes_txt, path_to_data_yaml)

print('\nFile contents:\n')

file_path = Path("data/data.yaml")

with open(file_path, "r", encoding="utf-8") as f:
    print(f.read())

Created config file at data/data.yaml

File contents:

path: data
train: train/images
val: validation/images
nc: 11
names:
- 01_Good
- 10_Overhang_Sag
- 11_Shifted_Layer
- 12_Warping
- 13_Delamination
- 14_Unclear
- 15_Not_Printing
- 4_Foreign_Body
- 6_Stringing
- 7_Spaghetti
- 9_Poor_Bridging



In [8]:
yaml_text = """path: data
train: train/images
val: val/images
test: test/images

nc: 11
names:
  0: 01_Good
  1: 4_Foreign_Body
  2: 6_Stringing
  3: 7_Spaghetti
  4: 9_Poor_Bridging
  5: 10_Overhang_Sag
  6: 11_Shifted_Layer
  7: 12_Warping
  8: 13_Delamination
  9: 14_Unclear
  10: 15_Not_Printing
"""

Path("data/data.yaml").write_text(yaml_text, encoding="utf-8")
print(Path("data/data.yaml").read_text(encoding="utf-8"))

path: data
train: train/images
val: val/images
test: test/images

nc: 11
names:
  0: 01_Good
  1: 4_Foreign_Body
  2: 6_Stringing
  3: 7_Spaghetti
  4: 9_Poor_Bridging
  5: 10_Overhang_Sag
  6: 11_Shifted_Layer
  7: 12_Warping
  8: 13_Delamination
  9: 14_Unclear
  10: 15_Not_Printing



In [6]:
from pathlib import Path
from collections import Counter

root = Path("data")
label_files = list(root.rglob("labels/*.txt")) + list(root.rglob("**/labels/**/*.txt"))
print("Found label files:", len(label_files))

counts = Counter()
max_id = -1

for f in label_files:
    for line in f.read_text(encoding="utf-8", errors="ignore").splitlines():
        if not line.strip():
            continue
        cls = int(float(line.split()[0]))
        counts[cls] += 1
        max_id = max(max_id, cls)

print("Class IDs present:", sorted(counts.keys()))
print("Max class ID:", max_id)
print("Counts:", dict(sorted(counts.items())))

Found label files: 6272
Class IDs present: [1, 2, 3, 4, 5, 6, 7, 8]
Max class ID: 8
Counts: {1: 2070, 2: 1118, 3: 1214, 4: 836, 5: 2492, 6: 1064, 7: 1326, 8: 3126}


In [7]:
import sys, torch
import ultralytics

print("Python exe:", sys.executable)
print("Torch version:", torch.__version__)
print("CUDA available:", torch.cuda.is_available())
print("CUDA device count:", torch.cuda.device_count())
print("CUDA device name:", torch.cuda.get_device_name(0) if torch.cuda.is_available() else None)
print("Ultralytics version:", ultralytics.__version__)

Python exe: c:\Program Files\Python312\python.exe
Torch version: 2.5.1+cu121
CUDA available: True
CUDA device count: 1
CUDA device name: NVIDIA GeForce RTX 4060 Laptop GPU
Ultralytics version: 8.3.229


In [2]:
DATA_YAML = "data/data.yaml"
BASE_MODEL = "yolov8s.pt" 
DEVICE = 0                        
PROJECT = "runs/gridsearch_final"       
GRID_EPOCHS = 5
FIXED_IMGSZ = 640                        
SEED = 42

Hyperparameter tuning with Grid-Search

In [2]:
from ultralytics import YOLO
from pathlib import Path
import itertools
import pandas as pd
import time

# CONFIG
DATA_YAML = "data/data.yaml"
BASE_MODEL = "yolov8s.pt"          
DEVICE = 0                        
PROJECT = "runs/gridsearch_final"       
GRID_EPOCHS = 5
FIXED_IMGSZ = 640                        
SEED = 42

# GRID SETUP
grid = {
    "lr0": [0.01, 0.001, 0.0001],
    "weight_decay": [0.0005, 0.005, 0.05],
    "box": [5, 7.5, 10],
    "cls": [0.25, 0.5],
    "freeze": [5, 6, 7, 8, 9]
}

Path(PROJECT).mkdir(parents=True, exist_ok=True)

keys = list(grid.keys())
combos = list(itertools.product(*[grid[k] for k in keys]))
print(f"Total runs: {len(combos)}")

rows = []
t0 = time.time()

for i, values in enumerate(combos, start=1):
    params = dict(zip(keys, values))
    run_name = "gs_" + "_".join([f"{k}={v}" for k, v in params.items()])

    print(f"\n[{i}/{len(combos)}] Training: {run_name}")
    model = YOLO(BASE_MODEL)

    train_results = model.train(
        data=DATA_YAML,
        epochs=GRID_EPOCHS,
        imgsz=FIXED_IMGSZ,
        lr0=params["lr0"],
        weight_decay=params["weight_decay"],
        optimizer="AdamW",
        box=params["box"],
        freeze=params["freeze"],
        batch=16,
        device=DEVICE,
        seed=SEED,
        deterministic=True,
        project=PROJECT,
        name=run_name,
        plots=False,           # faster
        save=True,
        val=True,
        patience=4            # early stopping helps speed grid search
    )

# After training, evaluate the best checkpoint on val to get a clean final score
    best_path = Path(model.trainer.save_dir) / "weights" / "best.pt"
    best_model = YOLO(str(best_path))
    val_metrics = best_model.val(data=DATA_YAML, split="val", device=DEVICE, plots=False)

    # Extract metrics (these attribute names are stable in Ultralytics v8.x)
    row = {
        "run_name": run_name,
        "save_dir": str(model.trainer.save_dir),
        "best_pt": str(best_path),
        **params,
        "imgsz": params.get("imgsz", FIXED_IMGSZ),
        "val_mAP50_95": float(val_metrics.box.map),     # mAP@[.5:.95]
        "val_mAP50": float(val_metrics.box.map50),      # mAP@.5
        "val_precision": float(val_metrics.box.mp),     # mean precision
        "val_recall": float(val_metrics.box.mr),        # mean recall
    }
    rows.append(row)

 # Write partial results continuously (so you don’t lose progress)
    df = pd.DataFrame(rows).sort_values("val_mAP50_95", ascending=False)
    df.to_csv(Path(PROJECT) / "grid_results.csv", index=False)

print(f"\nDone in {(time.time()-t0)/60:.1f} minutes.")
df.head(10)

Total runs: 270

[1/270] Training: gs_lr0=0.01_weight_decay=0.0005_box=5_cls=0.25_freeze=5
New https://pypi.org/project/ultralytics/8.4.7 available  Update with 'pip install -U ultralytics'
Ultralytics 8.3.229  Python-3.12.3 torch-2.5.1+cu121 CUDA:0 (NVIDIA GeForce RTX 4060 Laptop GPU, 8188MiB)
engine\trainer: agnostic_nms=False, amp=True, augment=False, auto_augment=randaugment, batch=16, bgr=0.0, box=5, cache=False, cfg=None, classes=None, close_mosaic=10, cls=0.5, compile=False, conf=None, copy_paste=0.0, copy_paste_mode=flip, cos_lr=False, cutmix=0.0, data=data/data.yaml, degrees=0.0, deterministic=True, device=0, dfl=1.5, dnn=False, dropout=0.0, dynamic=False, embed=None, epochs=5, erasing=0.4, exist_ok=False, fliplr=0.5, flipud=0.0, format=torchscript, fraction=1.0, freeze=5, half=False, hsv_h=0.015, hsv_s=0.7, hsv_v=0.4, imgsz=640, int8=False, iou=0.7, keras=False, kobj=1.0, line_width=None, lr0=0.01, lrf=0.01, mask_ratio=4, max_det=300, mixup=0.0, mode=train, model=yolov8s.pt, 

run_name  \
150  gs_lr0=0.001_weight_decay=0.05_box=5_cls=0.25_...   
155  gs_lr0=0.001_weight_decay=0.05_box=5_cls=0.5_f...   
136  gs_lr0=0.001_weight_decay=0.005_box=7.5_cls=0....   
131  gs_lr0=0.001_weight_decay=0.005_box=7.5_cls=0....   
124  gs_lr0=0.001_weight_decay=0.005_box=5_cls=0.25...   
129  gs_lr0=0.001_weight_decay=0.005_box=5_cls=0.5_...   
156  gs_lr0=0.001_weight_decay=0.05_box=5_cls=0.5_f...   
151  gs_lr0=0.001_weight_decay=0.05_box=5_cls=0.25_...   
95   gs_lr0=0.001_weight_decay=0.0005_box=5_cls=0.5...   
90   gs_lr0=0.001_weight_decay=0.0005_box=5_cls=0.2...   

                                              save_dir  \
150  C:\Users\User\Documents\GitHub\Real-Time-Defec...   
155  C:\Users\User\Documents\GitHub\Real-Time-Defec...   
136  C:\Users\User\Documents\GitHub\Real-Time-Defec...   
131  C:\Users\User\Documents\GitHub\Real-Time-Defec...   
124  C:\Users\User\Documents\GitHub\Real-Time-Defec...   
129  C:\Users\User\Documents\GitHub\Real-Time-Defec...   
156  C:\Users\User\Documents\GitHub\Real-Time-Defec...   
151  C:\Users\User\Documents\GitHub\Real-Time-Defec...   
95   C:\Users\User\Documents\GitHub\Real-Time-Defec...   
90   C:\Users\User\Documents\GitHub\Real-Time-Defec...   

                                               best_pt    lr0  weight_decay  \
150  C:\Users\User\Documents\GitHub\Real-Time-Defec...  0.001        0.0500   
155  C:\Users\User\Documents\GitHub\Real-Time-Defec...  0.001        0.0500   
136  C:\Users\User\Documents\GitHub\Real-Time-Defec...  0.001        0.0050   
131  C:\Users\User\Documents\GitHub\Real-Time-Defec...  0.001        0.0050   
124  C:\Users\User\Documents\GitHub\Real-Time-Defec...  0.001        0.0050   
129  C:\Users\User\Documents\GitHub\Real-Time-Defec...  0.001        0.0050   
156  C:\Users\User\Documents\GitHub\Real-Time-Defec...  0.001        0.0500   
151  C:\Users\User\Documents\GitHub\Real-Time-Defec...  0.001        0.0500   
95   C:\Users\User\Documents\GitHub\Real-Time-Defec...  0.001        0.0005   
90   C:\Users\User\Documents\GitHub\Real-Time-Defec...  0.001        0.0005   

     box   cls  freeze  imgsz  val_mAP50_95  val_mAP50  val_precision  \
150  5.0  0.25       5    640      0.398987   0.723295       0.705241   
155  5.0  0.50       5    640      0.398987   0.723295       0.705241   
136  7.5  0.50       6    640      0.398105   0.715871       0.698586   
131  7.5  0.25       6    640      0.398105   0.715871       0.698586   
124  5.0  0.25       9    640      0.395551   0.727278       0.720713   
129  5.0  0.50       9    640      0.395551   0.727278       0.720713   
156  5.0  0.50       6    640      0.395194   0.718967       0.713676   
151  5.0  0.25       6    640      0.395194   0.718967       0.713676   
95   5.0  0.50       5    640      0.394661   0.720820       0.705915   
90   5.0  0.25       5    640      0.394661   0.720820       0.705915   

     val_recall  
150    0.693155  
155    0.693155  
136    0.698634  
131    0.698634  
124    0.681746  
129    0.681746  
156    0.684402  
151    0.684402  
95     0.674875  
90     0.674875

In [ ]:
from ultralytics import YOLO
from pathlib import Path
import itertools
import pandas as pd
import time

# CONFIG
DATA_YAML = "data/data.yaml"
BASE_MODEL = "yolov8s.pt"          
DEVICE = 0                        
PROJECT = "runs/gridsearch_final_new"       
GRID_EPOCHS = 5
FIXED_IMGSZ = 640                        
SEED = 42

# GRID SETUP
grid = {
    "freeze": [3, 4, 5]
}

Path(PROJECT).mkdir(parents=True, exist_ok=True)

keys = list(grid.keys())
combos = list(itertools.product(*[grid[k] for k in keys]))
print(f"Total runs: {len(combos)}")

rows = []
t0 = time.time()

for i, values in enumerate(combos, start=1):
    params = dict(zip(keys, values))
    run_name = "gs_" + "_".join([f"{k}={v}" for k, v in params.items()])

    print(f"\n[{i}/{len(combos)}] Training: {run_name}")
    model = YOLO(BASE_MODEL)

    # Best parameters are inputted from the previous grid-search
    train_results = model.train(
        data=DATA_YAML,
        epochs=GRID_EPOCHS,
        imgsz=FIXED_IMGSZ,
        lr0=0.001,
        weight_decay=0.05,
        optimizer="AdamW",
        box=5,
        cls=0.25,
        freeze=params["freeze"],
        batch=16,
        device=DEVICE,
        seed=SEED,
        deterministic=True,
        project=PROJECT,
        name=run_name,
        plots=False,           # faster
        save=True,
        val=True,
        patience=4            # early stopping helps speed grid search
    )

# After training, evaluate the best checkpoint on val to get a clean final score
    best_path = Path(model.trainer.save_dir) / "weights" / "best.pt"
    best_model = YOLO(str(best_path))
    val_metrics = best_model.val(data=DATA_YAML, split="val", device=DEVICE, plots=False)

    # Extract metrics (these attribute names are stable in Ultralytics v8.x)
    row = {
        "run_name": run_name,
        "save_dir": str(model.trainer.save_dir),
        "best_pt": str(best_path),
        **params,
        "imgsz": params.get("imgsz", FIXED_IMGSZ),
        "val_mAP50_95": float(val_metrics.box.map),     # mAP@[.5:.95]
        "val_mAP50": float(val_metrics.box.map50),      # mAP@.5
        "val_precision": float(val_metrics.box.mp),     # mean precision
        "val_recall": float(val_metrics.box.mr),        # mean recall
    }
    rows.append(row)

 # Write partial results continuously (so you don’t lose progress)
    df = pd.DataFrame(rows).sort_values("val_mAP50_95", ascending=False)
    df.to_csv(Path(PROJECT) / "grid_results.csv", index=False)

print(f"\nDone in {(time.time()-t0)/60:.1f} minutes.")
df.head(10)

Total runs: 3

[1/3] Training: gs_lr0=0.001_weight_decay=0.05_box=5_cls=0.25_freeze=3
Ultralytics 8.3.229  Python-3.12.3 torch-2.5.1+cu121 CUDA:0 (NVIDIA GeForce RTX 4060 Laptop GPU, 8188MiB)
engine\trainer: agnostic_nms=False, amp=True, augment=False, auto_augment=randaugment, batch=16, bgr=0.0, box=5, cache=False, cfg=None, classes=None, close_mosaic=10, cls=0.5, compile=False, conf=None, copy_paste=0.0, copy_paste_mode=flip, cos_lr=False, cutmix=0.0, data=data/data.yaml, degrees=0.0, deterministic=True, device=0, dfl=1.5, dnn=False, dropout=0.0, dynamic=False, embed=None, epochs=5, erasing=0.4, exist_ok=False, fliplr=0.5, flipud=0.0, format=torchscript, fraction=1.0, freeze=3, half=False, hsv_h=0.015, hsv_s=0.7, hsv_v=0.4, imgsz=640, int8=False, iou=0.7, keras=False, kobj=1.0, line_width=None, lr0=0.001, lrf=0.01, mask_ratio=4, max_det=300, mixup=0.0, mode=train, model=yolov8s.pt, momentum=0.937, mosaic=1.0, multi_scale=False, name=gs_lr0=0.001_weight_decay=0.05_box=5_cls=0.25_freez

run_name  \
2  gs_lr0=0.001_weight_decay=0.05_box=5_cls=0.25_...   
0  gs_lr0=0.001_weight_decay=0.05_box=5_cls=0.25_...   
1  gs_lr0=0.001_weight_decay=0.05_box=5_cls=0.25_...   

                                            save_dir  \
2  C:\Users\User\Documents\GitHub\Real-Time-Defec...   
0  C:\Users\User\Documents\GitHub\Real-Time-Defec...   
1  C:\Users\User\Documents\GitHub\Real-Time-Defec...   

                                             best_pt    lr0  weight_decay  \
2  C:\Users\User\Documents\GitHub\Real-Time-Defec...  0.001          0.05   
0  C:\Users\User\Documents\GitHub\Real-Time-Defec...  0.001          0.05   
1  C:\Users\User\Documents\GitHub\Real-Time-Defec...  0.001          0.05   

   box   cls  freeze  imgsz  val_mAP50_95  val_mAP50  val_precision  \
2    5  0.25       5    640      0.398987   0.723295       0.705241   
0    5  0.25       3    640      0.391551   0.733269       0.684223   
1    5  0.25       4    640      0.391329   0.722306       0.674665   

   val_recall  
2    0.693155  
0    0.710063  
1    0.705684

In [4]:
from ultralytics import YOLO
import pandas as pd
from pathlib import Path

PROJECT = "runs/gridsearch_final"

df = pd.read_csv(Path(PROJECT) / "grid_results.csv").sort_values("val_mAP50_95", ascending=False)
best = df.iloc[0].to_dict()
print("Best config:", best)

final_name = "train_final"
model = YOLO(BASE_MODEL)
model.train(data="data/data.yaml",
            epochs=200,
            imgsz=FIXED_IMGSZ,
            lr0=float(best["lr0"]),
            weight_decay=float(best["weight_decay"]),
            optimizer="AdamW",
            box=float(best["box"]),
            freeze=int(best["freeze"]),
            cls=float(best["cls"]),
            batch=16,
            device=DEVICE,
            seed=SEED,
            deterministic=True,
            project="runs/detect",
            name=final_name,
            plots=True,
            val=True,
            patience=100,
            translate=0.2           
)

best_path = Path(model.trainer.save_dir) / "weights" / "best.pt"
last_path = Path(model.trainer.save_dir) / "weights" / "last.pt"
print("✅ Best checkpoint:", best_path)
print("✅ Last checkpoint:", last_path)

Best config: {'run_name': 'gs_lr0=0.001_weight_decay=0.05_box=5_cls=0.25_freeze=5', 'save_dir': 'C:\\Users\\User\\Documents\\GitHub\\Real-Time-Defect-Detection-Capstone-Project\\runs\\gridsearch_final\\gs_lr0=0.001_weight_decay=0.05_box=5_cls=0.25_freeze=5', 'best_pt': 'C:\\Users\\User\\Documents\\GitHub\\Real-Time-Defect-Detection-Capstone-Project\\runs\\gridsearch_final\\gs_lr0=0.001_weight_decay=0.05_box=5_cls=0.25_freeze=5\\weights\\best.pt', 'lr0': 0.001, 'weight_decay': 0.05, 'box': 5.0, 'cls': 0.25, 'freeze': 5, 'imgsz': 640, 'val_mAP50_95': 0.3989866935244932, 'val_mAP50': 0.7232954067937374, 'val_precision': 0.7052413289210446, 'val_recall': 0.6931546159258481}
Ultralytics 8.3.229  Python-3.12.3 torch-2.5.1+cu121 CUDA:0 (NVIDIA GeForce RTX 4060 Laptop GPU, 8188MiB)
engine\trainer: agnostic_nms=False, amp=True, augment=False, auto_augment=randaugment, batch=16, bgr=0.0, box=5.0, cache=False, cfg=None, classes=None, close_mosaic=10, cls=0.25, compile=False, conf=None, copy_paste

In [5]:
model = YOLO("runs/detect/train_final/weights/best.pt")

In [6]:
model.predict(source="data/val/images",
              save=True,
              name="val"
)

print("✅ Saved validation predictions under runs/detect/predict*")


image 1/250 c:\Users\User\Documents\GitHub\Real-Time-Defect-Detection-Capstone-Project\data\val\images\00624767-right_77photo_2024-10-04T11_08_33-787900.jpg: 416x640 1 7_Spaghetti, 54.3ms
image 2/250 c:\Users\User\Documents\GitHub\Real-Time-Defect-Detection-Capstone-Project\data\val\images\00b9f800-left_163photo_2024-10-02T14_05_41-353505.jpg: 416x640 1 6_Stringing, 18.0ms
image 3/250 c:\Users\User\Documents\GitHub\Real-Time-Defect-Detection-Capstone-Project\data\val\images\0116188c-left_67photo_2024-10-02T13_11_10-9292.jpg: 416x640 (no detections), 19.0ms
image 4/250 c:\Users\User\Documents\GitHub\Real-Time-Defect-Detection-Capstone-Project\data\val\images\012f441e-left_photo_57_2024-10-22_16-54-09.jpg: 416x640 1 13_Delamination, 19.2ms
image 5/250 c:\Users\User\Documents\GitHub\Real-Time-Defect-Detection-Capstone-Project\data\val\images\01491492-157photo_2024-08-21T16_29_57-15868.jpg: 416x640 2 12_Warpings, 22.0ms
image 6/250 c:\Users\User\Documents\GitHub\Real-Time-Defect-Detection

In [16]:
from ultralytics import YOLO

model = YOLO("runs/detect/train_final/weights/best.pt")

In [7]:
model.predict(
    source="data/test/images",  # wherever your test images are
    save=True,
    name="test",
    save_txt=True,     # saves YOLO-format predictions (class x y w h conf) per image
    save_conf=True
)


image 1/300 c:\Users\User\Documents\GitHub\Real-Time-Defect-Detection-Capstone-Project\data\test\images\00624767-right_77photo_2024-10-04T11_08_33-787900.jpg: 416x640 1 7_Spaghetti, 13.5ms
image 2/300 c:\Users\User\Documents\GitHub\Real-Time-Defect-Detection-Capstone-Project\data\test\images\009529f9-right_photo_182_2024-10-22_17-27-24.jpg: 416x640 5 13_Delaminations, 6.5ms
image 3/300 c:\Users\User\Documents\GitHub\Real-Time-Defect-Detection-Capstone-Project\data\test\images\00a8a190-left_1750photo_2024-08-27T17_19_02-958622.jpg: 416x640 4 4_Foreign_Bodys, 5.5ms
image 4/300 c:\Users\User\Documents\GitHub\Real-Time-Defect-Detection-Capstone-Project\data\test\images\027bae6a-left_photo_245_2024-11-21_18-00-35.jpg: 416x640 4 4_Foreign_Bodys, 4.7ms
image 5/300 c:\Users\User\Documents\GitHub\Real-Time-Defect-Detection-Capstone-Project\data\test\images\042994e7-left_right_181photo_2024-10-02T14_43_58-554388.jpg: 416x640 2 6_Stringings, 5.0ms
image 6/300 c:\Users\User\Documents\GitHub\Real-

[ultralytics.engine.results.Results object with attributes:
 
 boxes: ultralytics.engine.results.Boxes object
 keypoints: None
 masks: None
 names: {0: '01_Good', 1: '4_Foreign_Body', 2: '6_Stringing', 3: '7_Spaghetti', 4: '9_Poor_Bridging', 5: '10_Overhang_Sag', 6: '11_Shifted_Layer', 7: '12_Warping', 8: '13_Delamination', 9: '14_Unclear', 10: '15_Not_Printing'}
 obb: None
 orig_img: array([[[ 28,  24,  23],
         [ 28,  24,  23],
         [ 28,  24,  23],
         ...,
         [ 55,  53,  52],
         [ 55,  53,  52],
         [ 55,  53,  52]],
 
        [[ 29,  25,  24],
         [ 28,  24,  23],
         [ 28,  24,  23],
         ...,
         [ 54,  52,  51],
         [ 54,  52,  51],
         [ 54,  52,  51]],
 
        [[ 29,  25,  24],
         [ 29,  25,  24],
         [ 28,  24,  23],
         ...,
         [ 54,  52,  51],
         [ 54,  52,  51],
         [ 53,  51,  50]],
 
        ...,
 
        [[199, 197, 187],
         [204, 202, 192],
         [201, 199, 189],
 

In [8]:
model.val(data="data/data.yaml",
          split="test",
          device=0,
          name="test_metrics"
)

print("✅ Test evaluation complete.")

Ultralytics 8.3.229  Python-3.12.3 torch-2.5.1+cu121 CUDA:0 (NVIDIA GeForce RTX 4060 Laptop GPU, 8188MiB)
val: Fast image access  (ping: 0.10.0 ms, read: 1234.6256.0 MB/s, size: 290.4 KB)
val: Scanning C:\Users\User\Documents\GitHub\Real-Time-Defect-Detection-Capstone-Project\data\test\labels.cache... 300 images, 8 backgrounds, 0 corrupt: 100% ━━━━━━━━━━━━ 300/300 208.9Kit/s 0.0s
                 Class     Images  Instances      Box(P          R      mAP50  mAP50-95): 100% ━━━━━━━━━━━━ 19/19 7.1it/s 2.7s0.1s
                   all        300        700      0.842      0.693      0.739      0.495
        4_Foreign_Body         37        104      0.844      0.885      0.881      0.546
           6_Stringing         42         84      0.864       0.69      0.741      0.493
           7_Spaghetti         43         79       0.81      0.709      0.708       0.53
       9_Poor_Bridging         44         63      0.903      0.889      0.913      0.629
       10_Overhang_Sag         56        